In [6]:
import pandas as pd
pd.set_option('display.max_columns', 500)
import geopandas as gpd 
import matplotlib.pyplot as plt
# import folium 
from shapely.ops import nearest_points
from shapely.geometry import LineString

In [7]:
deaths = gpd.read_file("../migrant_deaths_analysis/death_files/ogis_migrant_deaths_091021_with_yuma.geojson")
deaths

deaths=deaths[deaths['Latitude'].notnull()]




In [8]:


deaths = gpd.read_file("../migrant_deaths_analysis/death_files/ogis_migrant_deaths_091021_with_yuma.geojson")

deaths['Latitude']= deaths.Latitude.astype(float)
deaths['Longitude']= deaths.Longitude.astype(float)
deaths = gpd.GeoDataFrame(deaths, geometry=gpd.points_from_xy(deaths.Longitude,deaths.Latitude))

deaths = deaths.set_crs('epsg:4326')



deaths['Reporting Date']= pd.to_datetime(deaths['Reporting Date'])
deaths['Reporting_year']= pd.to_datetime(deaths['Reporting Date']).dt.year



print(deaths.total_bounds)

print(deaths.total_bounds[0])
print(deaths.total_bounds[1])


minx, miny, maxx, maxy = deaths.total_bounds

[-114.80891    31.33271  -109.053383   33.94276 ]
-114.80891
31.33271


In [9]:
deaths

ML Number                           Name     Sex Age Reporting Date  \
0     00-00097                   Unidentified    male         2000-01-10   
1     00-00148                 Nicolas, Tomas    male  17     2000-01-22   
2     00-00189                   Unidentified    male         2000-01-20   
3     00-00222                   Unidentified    male         2000-01-10   
4     00-00245  Candia-Bravo, Maria Del Rocio  female  20     2000-02-05   
...        ...                            ...     ...  ..            ...   
3905      None                           None  Female  10     2021-08-25   
3906      None                           None    Male  25     2021-08-27   
3907      None                           None    Male  21     2021-08-30   
3908      None                           None    Male  31     2021-08-31   
3909      None                           None    Male  22     2021-08-31   

              Surface Management Location  \
0     Cocopah Indian Reservation            
1               State of Arizona            
2              US Forest Service            
3                        Private            
4           Tohono Oodham Nation            
...                          ...      ...   
3905                        Yuma     None   
3906       Barry Goldwater Range     None   
3907       Barry Goldwater Range     None   
3908               Cabeza Prieta     None   
3909               Cabeza Prieta     None   

                                     Location Precision Corridor Code  \
0     physical description with directions, distance...            12   
1     physical description with directions, distance...             4   
2     physical description with directions, distance...             5   
3     physical description with directions, distance...             9   
4     physical description with directions, distance...             7   
...                                                 ...           ...   
3905                                               None          None   
3906                                               None          None   
3907                                               None          None   
3908                                               None          None   
3909                                               None          None   

        Corridor                    Cause of Death  \
0           Yuma                              None   
1      Patagonia                              None   
2        Nogales                              None   
3            Ajo                              None   
4     San Miguel                              None   
...          ...                               ...   
3905        None        Exposure, high temperature   
3906        None        Exposure, high temperature   
3907        None        Exposure, high temperature   
3908        None  UNDETERMINED - SKELETAL REMAINS    
3909        None  UNDETERMINED - SKELETAL REMAINS    

                                 OME Determined COD Condition Code  \
0     UNDETERMINED - MUMMIFIED AND SKELETAL REMAINS              4   
1                                       HYPOTHERMIA              1   
2                   UNDETERMINED - SKELETAL REMAINS              7   
3                   UNDETERMINED - SKELETAL REMAINS              6   
4                     MULTIPLE BLUNT FORCE INJURIES              1   
...                                             ...            ...   
3905                                           None           None   
3906                                           None           None   
3907                                           None           None   
3908                                           None           None   
3909                                           None           None   

                                    Body Condition Post Mortem Interval  \
0                 Skeletonization w/ mummification           < 5 weeks    
1                                 

In [10]:
import requests
import urllib
import codecs
import json
from osm2geojson import json2geojson

OVERPASS = "https://overpass-api.de/api/interpreter/"


def overpass_call(query):
    encoded = urllib.parse.quote(query.encode('utf-8'), safe='~()*!.\'')
    r = requests.post(OVERPASS,
                      data=f"data={encoded}",
                      headers={'Content-Type': 'application/x-www-form-urlencoded; charset=UTF-8',
                              'User-Agent': 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10.9; rv:50.0) Gecko/20100101 Firefox/50.0'})
    if not r.status_code is 200:
        raise requests.exceptions.HTTPError('Overpass server respond with status '+str(r.status_code))
    return r.text


def save_data(data, geom_file):
    json_data = json.dumps(data, indent=2)
    f = codecs.open(geom_file, 'w')
    f.write(json_data)
    f.close()


data = overpass_call(f"""
    [out:json];
    (node["highway"="tertiary"]({miny},{minx},{maxy},{maxx});
    way["highway"="tertiary"]({miny},{minx},{maxy},{maxx});
    relation["highway"="tertiary"]({miny},{minx},{maxy},{maxx});
    
    node["highway"="secondary"]({miny},{minx},{maxy},{maxx});
    way["highway"="secondary"]({miny},{minx},{maxy},{maxx});
    relation["highway"="secondary"]({miny},{minx},{maxy},{maxx});
    
    node["highway"="primary"]({miny},{minx},{maxy},{maxx});
    way["highway"="primary"]({miny},{minx},{maxy},{maxx});
    relation["highway"="primary"]({miny},{minx},{maxy},{maxx});
    
    node["highway"="trunk"]({miny},{minx},{maxy},{maxx});
    way["highway"="trunk"]({miny},{minx},{maxy},{maxx});
    relation["highway"="trunk"]({miny},{minx},{maxy},{maxx});

    node["highway"="motorway"]({miny},{minx},{maxy},{maxx});
    way["highway"="motorway"]({miny},{minx},{maxy},{maxx});
    relation["highway"="motorway"]({miny},{minx},{maxy},{maxx});
    
    )
    ;out geom;
""")

# print(geojson_data)
geojson_data = json2geojson(data)
save_data(geojson_data, '../migrant_deaths_analysis/distance_from_roads_towns_border/roads/roads.geojson')




dfff = gpd.read_file('../migrant_deaths_analysis/distance_from_roads_towns_border/roads/roads.geojson', driver='GeoJSON')
dfff = dfff.set_crs('epsg:4326')
dfff = dfff.to_crs('epsg:26912')
dfff

tags = dfff['tags'].apply(pd.Series)


fdd= dfff.merge(tags, left_index=True, right_index=True)
fdd

type_x         id                                               tags  \
0        way    5052829  {'adot_name': 'Benson-Steins Pass Highway', 'b...   
1        way    5052830  {'adot_name': 'Benson-Steins Pass Highway', 'b...   
2        way    5052927  {'adot_name': 'Benson-Steins Pass Highway', 'b...   
3        way    5053100  {'adot_name': 'Tucson-Benson Highway', 'bicycl...   
4        way    5053101  {'adot_name': 'Tucson-Benson Highway', 'bicycl...   
...      ...        ...                                                ...   
81882    way  990424963  {'adot_name': 'Phoenix-Cordes Junction Highway...   
81883    way  990425662  {'cycleway': 'lane', 'highway': 'primary', 'la...   
81884    way  990427390  {'adot_name': 'Phoenix-Cordes Junction Highway...   
81885    way  990427391  {'adot_name': 'Phoenix-Cordes Junction Highway...   
81886    way  990429870  {'adot_name': 'Phoenix-Cordes Junction Highway...   

                                                geometry  \
0      LINESTRING (606101.591 3566208.687, 606124.984...   
1      LINESTRING (589804.025 3550043.112, 589838.952...   
2      LINESTRING (585660.459 3545528.967, 585688.678...   
3      LINESTRING (545904.722 3538025.446, 546075.027...   
4      LINESTRING (545861.887 3538043.831, 545904.722...   
...                                                  ...   
81882  LINESTRING (393931.058 3748944.566, 393933.440...   
81883  LINESTRING (414071.619 3716057.260, 414071.706...   
81884  LINESTRING (395563.482 3736433.785, 395518.241...   
81885  LINESTRING (395584.002 3736290.162, 395563.482...   
81886  LINESTRING (394214.620 3753741.141, 394230.826...   

                             adot_name bicycle         hgv   highway lanes  \
0           Benson-Steins Pass Highway     yes  designated  motorway     2   
1           Benson-Steins Pass Highway     yes  designated  motorway     2   
2           Benson-Steins Pass Highway     yes  designated  motorway     2   
3                Tucson-Benson Highway     yes  designated  motorway     2   
4                Tucson-Benson Highway     yes  designated  motorway     2   
...                                ...     ...         ...       ...   ...   
81882  Phoenix-Cordes Junction Highway     yes  designated  motorway     2   
81883                              NaN     NaN         NaN   primary     4   
81884  Phoenix-Cordes Junction Highway     yes  designated  motorway     4   
81885  Phoenix-Cordes Junction Highway     yes  designated  motorway     5   
81886  Phoenix-Cordes Junction Highway     yes  designated  motorway     2   

      maxspeed             old_ref oneway          ref       source  surface  \
0          120  US 666 (old SR 81)    yes  I 10;US 191  Yahoo,TIGER  asphalt   
1       75 mph                 NaN    yes         I 10          NaN      NaN   
2          NaN                 NaN    yes         I 10          NaN      NaN   
3           75   US 80 (old AZ 86)    yes         I 10          NaN      NaN   
4           75   US 80 (old AZ 86)    yes         I 10          NaN      NaN   
...        ...                 ...    ...          ...          ...      ...   
81882   75 mph                 NaN    yes         I 17          NaN  asphalt   
81883      NaN                 NaN    yes          NaN          NaN  asphalt   
81884   65 mph                 NaN    yes         I 17          NaN  asphalt   
81885   65 mph                 NaN    yes         I 17          NaN  asphalt   
81886   75 mph                 NaN    yes         I 17          NaN  asphalt   

      bridge layer tiger:cfcc  tiger:county tiger:name_base tiger:reviewed  \
0        NaN   NaN        NaN           NaN             NaN            NaN   
1        NaN   NaN        NaN           NaN             NaN            NaN   
2        yes     1        NaN           NaN             NaN            NaN   
3        NaN   NaN        NaN           NaN             NaN            NaN   
4        yes     1        NaN           NaN             NaN 

In [11]:
dfff

type         id                                               tags  \
0      way    5052829  {'adot_name': 'Benson-Steins Pass Highway', 'b...   
1      way    5052830  {'adot_name': 'Benson-Steins Pass Highway', 'b...   
2      way    5052927  {'adot_name': 'Benson-Steins Pass Highway', 'b...   
3      way    5053100  {'adot_name': 'Tucson-Benson Highway', 'bicycl...   
4      way    5053101  {'adot_name': 'Tucson-Benson Highway', 'bicycl...   
...    ...        ...                                                ...   
81882  way  990424963  {'adot_name': 'Phoenix-Cordes Junction Highway...   
81883  way  990425662  {'cycleway': 'lane', 'highway': 'primary', 'la...   
81884  way  990427390  {'adot_name': 'Phoenix-Cordes Junction Highway...   
81885  way  990427391  {'adot_name': 'Phoenix-Cordes Junction Highway...   
81886  way  990429870  {'adot_name': 'Phoenix-Cordes Junction Highway...   

                                                geometry  
0      LINESTRING (606101.591 3566208.687, 606124.984...  
1      LINESTRING (589804.025 3550043.112, 589838.952...  
2      LINESTRING (585660.459 3545528.967, 585688.678...  
3      LINESTRING (545904.722 3538025.446, 546075.027...  
4      LINESTRING (545861.887 3538043.831, 545904.722...  
...                                                  ...  
81882  LINESTRING (393931.058 3748944.566, 393933.440...  
81883  LINESTRING (414071.619 3716057.260, 414071.706...  
81884  LINESTRING (395563.482 3736433.785, 395518.241...  
81885  LINESTRING (395584.002 3736290.162, 395563.482...  
81886  LINESTRING (394214.620 3753741.141, 394230.826...  

[81887 rows x 4 columns]

In [12]:
fdd['type_x'].value_counts(dropna=False)

way    81887
Name: type_x, dtype: int64

In [13]:
deaths = deaths.reset_index()

In [14]:

print(fdd.crs )
print(deaths.crs )
deaths = deaths.to_crs('epsg:26912')

fdd = fdd.to_crs('epsg:26912')



print(fdd.crs )
print(deaths.crs )


def calculate_nearest(row, lines):
    
    print(row['index'])
    distances1 = fdd.distance(row['geometry'])
    
    min_val=distances1.min()
    min_indices=[idx for idx,val in distances1.items() if val==min_val]
#     print(min_indices)
    
    if len(min_indices)>1:
        print('more than one min')
        print(len(min_indices))
        print('done')
    
    mins_list = []
    for mins in min_indices:
        border_seg1 = lines['id'][mins]
        mins_list.append(border_seg1)
    print(mins_list)
    return [min_val,mins_list]


    
#     print( row['geometry'][0])

deaths['road_distance'] = deaths.apply(lambda row : calculate_nearest(row, fdd),axis=1)
                                      
                                      
                                      
                                      
roads = deaths.road_distance.apply(pd.Series)
roads.columns = ['distance', 'IDs']                                       




# min_val=min(my_list)
# min_indices=[idx for idx,val in enumerate(my_list) if val==min_val]




# border_seg1 = border_lines['geometry'][min_idx1]

roads



epsg:26912
epsg:4326
epsg:26912
epsg:26912
0
[37902494]
1
[371300246]
2
[37447407]
3
[137333586]
4
[659616378]
5
[659616378]
6
[659616378]
7
[659616378]
8
[16929304]
9
[692077405]
10
[413702055]
11
[987950578]
12
[413702055]
13
[280145462]
14
[300402452]
15
[692077405]
16
[280152405]
17
more than one min
2
done
[16899603, 16910037]
18
[280145462]
19
[372552255]
20
[394530268]
21
[16909804]
22
[118807784]
23
[37449623]
24
[192028869]
25
[129986124]
26
[563496375]
27
[659616378]
28
[512236953]
29
[692077405]
30
[563106644]
31
[375641244]
32
[37447410]
33
[300340240]
34
[16900567]
35
[439763914]
36
[512236953]
37
[413702061]
38
[775174518]
39
[692077405]
40
[692077405]
41
[280145462]
42
[292984367]
43
[723914594]
44
[280152379]
45
[321267185]
46
[280152379]
47
[376904096]
48
[671854855]
49
[16929304]
50
[758378711]
51
[660960563]
52
[420145882]
53
[16915220]
54
[692077405]
55
[441082931]
56
[458503090]
57
[458503090]
58
[458503090]
59
[394530269]
60
[692077405]
61
[692077405]
62
[28015240

[16910037]
500
[280128686]
501
[660960563]
502
[16912589]
503
[280902600]
504
[527468888]
505
[16912604]
506
[16919075]
507
[16878322]
508
[545552594]
509
[16929304]
510
[527470629]
511
[333445300]
512
[333445300]
513
[333445300]
514
[16912589]
515
[16920744]
516
[32743949]
517
[188496182]
518
[744139201]
519
more than one min
2
done
[413702056, 867738998]
520
[393904148]
521
[16920195]
522
[16904579]
523
[280152405]
524
[280152405]
525
[280152379]
526
[413702627]
527
[16934417]
528
[536062006]
529
[147218336]
530
[147218336]
531
[371751235]
532
[16915220]
533
[16915220]
534
[280152405]
535
[16898233]
536
[660960563]
537
[280902600]
538
[30853274]
539
[280152379]
540
[659616378]
541
[16926103]
542
[659616378]
543
[512236953]
544
[908278815]
545
[563495927]
546
[563495927]
547
[288001451]
548
[393904148]
549
[280152379]
550
[16912604]
551
[16929304]
552
[16915220]
553
more than one min
2
done
[16904579, 16918631]
554
[393904148]
555
[16922043]
556
[16898233]
557
[586643113]
558
[2812766

[37447407]
992
[16945843]
993
[661002802]
994
[333445268]
995
[16906893]
996
[280145462]
997
more than one min
2
done
[17303647, 535528333]
998
[16921584]
999
[908278815]
1000
[16922593]
1001
[887374795]
1002
[16915220]
1003
[16915220]
1004
[16915220]
1005
[16915220]
1006
[276663947]
1007
[35342946]
1008
[16878322]
1009
[300541224]
1010
[458503090]
1011
[37447407]
1012
[105500689]
1013
more than one min
2
done
[16898233, 16906893]
1014
[333445300]
1015
more than one min
2
done
[16899603, 16910037]
1016
[692493037]
1017
[229580379]
1018
[16922031]
1019
[908278815]
1020
[908278815]
1021
[37447407]
1022
[660960563]
1023
[831360387]
1024
[16929252]
1025
[907474233]
1026
[16918125]
1027
[16918125]
1028
[16918125]
1029
[16934417]
1030
[439763912]
1031
[16946853]
1032
[280152379]
1033
[177396538]
1034
[375640831]
1035
[300340240]
1036
[770413544]
1037
[300350011]
1038
[798192001]
1039
[16922967]
1040
[660960563]
1041
[16913077]
1042
[16918631]
1043
[280152405]
1044
[16905439]
1045
[16873578]


[292984367]
1455
[292984367]
1456
[393904137]
1457
[219801327]
1458
[16878322]
1459
[723914594]
1460
[280152379]
1461
[280145462]
1462
[156749636]
1463
[156749636]
1464
[758347429]
1465
[435546708]
1466
[300584690]
1467
[311061897]
1468
[300340240]
1469
[256403380]
1470
[256403380]
1471
[16906893]
1472
[16929304]
1473
[535529524]
1474
[16922082]
1475
[16933845]
1476
[393904148]
1477
[16915220]
1478
[16915220]
1479
[280145462]
1480
[393904148]
1481
[207592406]
1482
[16912659]
1483
[192028869]
1484
[751217083]
1485
[16906893]
1486
[300541225]
1487
[16915220]
1488
[16926103]
1489
[16900567]
1490
more than one min
2
done
[16899603, 16910037]
1491
[660960563]
1492
[660960563]
1493
[105500689]
1494
[16878322]
1495
[413702055]
1496
[16907482]
1497
more than one min
2
done
[16918718, 16919661]
1498
[660960563]
1499
[659616378]
1500
[16915220]
1501
[16922593]
1502
[292984367]
1503
[292984367]
1504
[660960563]
1505
[311061897]
1506
[563495927]
1507
[27759413]
1508
[758696478]
1509
[692077405]
15

[563495927]
1925
[16915220]
1926
[177396560]
1927
[16898233]
1928
[16915220]
1929
more than one min
2
done
[16918718, 16919661]
1930
[16924403]
1931
[37447448]
1932
[16937494]
1933
[280145464]
1934
[16909804]
1935
more than one min
2
done
[16940898, 177396560]
1936
more than one min
2
done
[16940898, 177396560]
1937
more than one min
2
done
[16940898, 177396560]
1938
[16900567]
1939
[129986124]
1940
[758696478]
1941
[908278816]
1942
[300399842]
1943
[393904148]
1944
[35342907]
1945
[31054189]
1946
[393904148]
1947
[692077405]
1948
more than one min
2
done
[17303647, 535530618]
1949
[16929233]
1950
[16920195]
1951
[393904148]
1952
[16922082]
1953
[16909804]
1954
[16915220]
1955
[393904148]
1956
[393904148]
1957
[393904148]
1958
[280152379]
1959
[757290235]
1960
[16906893]
1961
[16929304]
1962
[535530618]
1963
[156749626]
1964
[660960563]
1965
[16922082]
1966
[16922306]
1967
[311061897]
1968
[311061897]
1969
[118121712]
1970
[280152379]
1971
[16912604]
1972
[16906893]
1973
[16946165]
197

...

[16922043]
3344
more than one min
2
done
[693735870, 694247442]
3345
[693723608]
3346
[37447190]
3347
[16943802]
3348
[280152405]
3349
[280152405]
3350
[16922593]
3351
[378098527]
3352
[16912659]
3353
[16878322]
3354
[280902589]
3355
[35342907]
3356
[774725744]
3357
[16912589]
3358
[393904148]
3359
[375641244]
3360
[512236953]
3361
[16906893]
3362
[660960563]
3363
[16900567]
3364
[16907482]
3365
[16929304]
3366
[393904148]
3367
[16929304]
3368
[105500689]
3369
[755577271]
3370
[16906893]
3371
[393904148]
3372
[177396560]
3373
[379246826]
3374
[16909804]
3375
[16929252]
3376
[660960563]
3377
[660960563]
3378
[129986124]
3379
[379246826]
3380
[723914594]
3381
[16906893]
3382
[393904148]
3383
[393904137]
3384
[280139477]
3385
[16900567]
3386
[16918125]
3387
[693723608]
3388
[659616378]
3389
[16912604]
3390
[16929304]
3391
[563495927]
3392
[16906893]
3393
[280139477]
3394
[16929304]
3395
[512236953]
3396
[16934417]
3397
[379246826]
3398
[16929304]
3399
[379210305]
3400
[524527078]
3401
[39

[759904806]
3817
[693708085]
3818
[545552594]
3819
[35340074]
3820
[35340074]
3821
more than one min
81887
done
[5052829, 5052830, 5052927, 5053100, 5053101, 5053102, 5053144, 5053145, 5053175, 5053177, 5053184, 5053192, 5053193, 5053204, 5053205, 5053207, 5053209, 5053271, 5053277, 5072114, 5560522, 5561288, 5561620, 5561638, 5562004, 5562181, 5562598, 5564543, 5565921, 5566195, 5568993, 5569117, 5569200, 5571955, 5572677, 5573620, 5575345, 5575486, 5575581, 5576614, 5576746, 5581098, 5582104, 5582106, 5582367, 5582717, 5585861, 5586139, 5587245, 5587284, 5587382, 5587464, 5587803, 5587980, 5588026, 5588078, 5588087, 5588231, 5588233, 5588421, 5588501, 5588512, 5588646, 5588719, 5588756, 5588779, 5588812, 5588893, 5589181, 5589483, 5589672, 5589756, 5589820, 5589841, 5589853, 5589856, 5589880, 5589925, 5590175, 5590351, 5590358, 5590766, 5590795, 5590796, 5590847, 5590887, 5590964, 5590967, 5590984, 5591127, 5591245, 5591314, 5591317, 5591385, 5591735, 5591767, 5591796, 5591809, 55918

[658346233]
3823
[658346233]
3824
[759016656]
3825
[35340684]
3826
more than one min
2
done
[207086109, 452803336]
3827
[541151801]
3828
[232408800]
3829
[759016656]
3830
[241411738]
3831
[153631634]
3832
[759016656]
3833
[207086109]
3834
[693735870]
3835
[207315418]
3836
[180485716]
3837
[759016656]
3838
[693735870]
3839
[693735870]
3840
more than one min
2
done
[207086109, 452803336]
3841
[550327495]
3842
[35340106]
3843
[35340977]
3844
[658346233]
3845
more than one min
2
done
[16958977, 724195270]
3846
[153631634]
3847
[759016656]
3848
[757274922]
3849
[693723608]
3850
[693723608]
3851
[232408800]
3852
[207315418]
3853
[209092644]
3854
[207315418]
3855
[658346233]
3856
[232408800]
3857
[693787450]
3858
[232408800]
3859
[658346233]
3860
[693735870]
3861
[37902494]
3862
[37902494]
3863
[160791075]
3864
[35340684]
3865
[693735870]
3866
[43523795]
3867
[280128686]
3868
[232408800]
3869
[824627848]
3870
[910062713]
3871
[770413544]
3872
[770413544]
3873
[546483224]
3874
[492039502]
3875

[546483224]
3897
[16949025]
3898
[693735870]
3899
[546483224]
3900
[35340684]
3901
[35340684]
3902
[177042227]
3903
[232408800]
3904
[43523795]
3905
[43523795]
3906
[546483224]
3907
[35340684]
3908
[693735870]
3909
[693735870]


distance          IDs
0      2818.309440   [37902494]
1      9813.136213  [371300246]
2      9166.868453   [37447407]
3         6.888744  [137333586]
4        18.968821  [659616378]
...            ...          ...
3905   1751.133199   [43523795]
3906   3622.989887  [546483224]
3907    797.015166   [35340684]
3908  36042.131013  [693735870]
3909  36009.293490  [693735870]

[3910 rows x 2 columns]

In [15]:
deaths_roads = roads.merge(deaths,left_index=True, right_index=True)
deaths_roads




# deaths

distance          IDs  index ML Number  \
0      2818.309440   [37902494]      0  00-00097   
1      9813.136213  [371300246]      1  00-00148   
2      9166.868453   [37447407]      2  00-00189   
3         6.888744  [137333586]      3  00-00222   
4        18.968821  [659616378]      4  00-00245   
...            ...          ...    ...       ...   
3905   1751.133199   [43523795]   3905      None   
3906   3622.989887  [546483224]   3906      None   
3907    797.015166   [35340684]   3907      None   
3908  36042.131013  [693735870]   3908      None   
3909  36009.293490  [693735870]   3909      None   

                               Name     Sex Age Reporting Date  \
0                      Unidentified    male         2000-01-10   
1                    Nicolas, Tomas    male  17     2000-01-22   
2                      Unidentified    male         2000-01-20   
3                      Unidentified    male         2000-01-10   
4     Candia-Bravo, Maria Del Rocio  female  20     2000-02-05   
...                             ...     ...  ..            ...   
3905                           None  Female  10     2021-08-25   
3906                           None    Male  25     2021-08-27   
3907                           None    Male  21     2021-08-30   
3908                           None    Male  31     2021-08-31   
3909                           None    Male  22     2021-08-31   

              Surface Management Location  \
0     Cocopah Indian Reservation            
1               State of Arizona            
2              US Forest Service            
3                        Private            
4           Tohono Oodham Nation            
...                          ...      ...   
3905                        Yuma     None   
3906       Barry Goldwater Range     None   
3907       Barry Goldwater Range     None   
3908               Cabeza Prieta     None   
3909               Cabeza Prieta     None   

                                     Location Precision Corridor Code  \
0     physical description with directions, distance...            12   
1     physical description with directions, distance...             4   
2     physical description with directions, distance...             5   
3     physical description with directions, distance...             9   
4     physical description with directions, distance...             7   
...                                                 ...           ...   
3905                                               None          None   
3906                                               None          None   
3907                                               None          None   
3908                                               None          None   
3909                                               None          None   

        Corridor                    Cause of Death  \
0           Yuma                              None   
1      Patagonia                              None   
2        Nogales                              None   
3            Ajo                              None   
4     San Miguel                              None   
...          ...                               ...   
3905        None        Exposure, high temperature   
3906        None        Exposure, high temperature   
3907        None        Exposure, high temperature   
3908        None  UNDETERMINED - SKELETAL REMAINS    
3909        None  UNDETERMINED - SKELETAL REMAINS    

                                 OME Determined COD Condition Code  \
0     UNDETERMINED - MUMMIFIED AND SKELETAL REMAINS              4   
1                                       HYPOTHERMIA              1   
2                   UNDETERMINED - SKELETAL REMAINS              7   
3                   UNDETERMINED - SKELETAL REMAINS              6   
4                     MULTIPLE BLUNT FORCE INJURIES              1   
...                                             ...            ...   
3905                               

In [16]:


def unpack(row):
    if len(row['IDs']) < 1:
        return None
    else:
        return row['IDs'][0]

def unpack2(row):
    if len(row['IDs']) < 2:
        return None
    else:
        return row['IDs'][1]
    

deaths_roads['unpacked_ID'] = deaths_roads.apply(lambda row : unpack(row),axis=1)

deaths_roads['unpacked_ID_2'] = deaths_roads.apply(lambda row : unpack2(row),axis=1)

deaths_roads_merged = deaths_roads.merge(fdd, left_on="unpacked_ID",right_on="id",how='left')


deaths_roads_merged

distance          IDs  index ML Number  \
0      2818.309440   [37902494]      0  00-00097   
1      9813.136213  [371300246]      1  00-00148   
2      9166.868453   [37447407]      2  00-00189   
3         6.888744  [137333586]      3  00-00222   
4        18.968821  [659616378]      4  00-00245   
...            ...          ...    ...       ...   
3905   1751.133199   [43523795]   3905      None   
3906   3622.989887  [546483224]   3906      None   
3907    797.015166   [35340684]   3907      None   
3908  36042.131013  [693735870]   3908      None   
3909  36009.293490  [693735870]   3909      None   

                               Name     Sex Age Reporting Date  \
0                      Unidentified    male         2000-01-10   
1                    Nicolas, Tomas    male  17     2000-01-22   
2                      Unidentified    male         2000-01-20   
3                      Unidentified    male         2000-01-10   
4     Candia-Bravo, Maria Del Rocio  female  20     2000-02-05   
...                             ...     ...  ..            ...   
3905                           None  Female  10     2021-08-25   
3906                           None    Male  25     2021-08-27   
3907                           None    Male  21     2021-08-30   
3908                           None    Male  31     2021-08-31   
3909                           None    Male  22     2021-08-31   

              Surface Management Location  \
0     Cocopah Indian Reservation            
1               State of Arizona            
2              US Forest Service            
3                        Private            
4           Tohono Oodham Nation            
...                          ...      ...   
3905                        Yuma     None   
3906       Barry Goldwater Range     None   
3907       Barry Goldwater Range     None   
3908               Cabeza Prieta     None   
3909               Cabeza Prieta     None   

                                     Location Precision Corridor Code  \
0     physical description with directions, distance...            12   
1     physical description with directions, distance...             4   
2     physical description with directions, distance...             5   
3     physical description with directions, distance...             9   
4     physical description with directions, distance...             7   
...                                                 ...           ...   
3905                                               None          None   
3906                                               None          None   
3907                                               None          None   
3908                                               None          None   
3909                                               None          None   

        Corridor                    Cause of Death  \
0           Yuma                              None   
1      Patagonia                              None   
2        Nogales                              None   
3            Ajo                              None   
4     San Miguel                              None   
...          ...                               ...   
3905        None        Exposure, high temperature   
3906        None        Exposure, high temperature   
3907        None        Exposure, high temperature   
3908        None  UNDETERMINED - SKELETAL REMAINS    
3909        None  UNDETERMINED - SKELETAL REMAINS    

                                 OME Determined COD Condition Code  \
0     UNDETERMINED - MUMMIFIED AND SKELETAL REMAINS              4   
1                                       HYPOTHERMIA              1   
2                   UNDETERMINED - SKELETAL REMAINS              7   
3                   UNDETERMINED - SKELETAL REMAINS              6   
4                     MULTIPLE BLUNT FORCE INJURIES              1   
...                                             ...            ...   
3905                               

In [17]:
13344073/1609.34

8291.643158064797

In [18]:


# deaths_roads_merged['road_distance_miles'] = (deaths_roads_merged['road_distance'].item()[0]/1609.34)

def unpack_meters2miles(row):
    
    print(row['road_distance'])
    print(row['road_distance'][0])
    return row['road_distance'][0]/1609.34

deaths_roads_merged['road_distance_miles'] = deaths_roads_merged.apply(lambda row : unpack_meters2miles(row),axis=1)


deaths_roads_merged


[2818.309439514846, [37902494]]
2818.309439514846
[9813.136212970445, [371300246]]
9813.136212970445
[9166.868452693176, [37447407]]
9166.868452693176
[6.88874406548814, [137333586]]
6.88874406548814
[18.968820627875377, [659616378]]
18.968820627875377
[23.471146196053994, [659616378]]
23.471146196053994
[42.02616708753616, [659616378]]
42.02616708753616
[37.52388151621053, [659616378]]
37.52388151621053
[5221.872043283293, [16929304]]
5221.872043283293
[161.67464472638738, [692077405]]
161.67464472638738
[12.108913939887614, [413702055]]
12.108913939887614
[5.291323914539185, [987950578]]
5.291323914539185
[529.0544685936882, [413702055]]
529.0544685936882
[12310.456289578618, [280145462]]
12310.456289578618
[22471.908389891396, [300402452]]
22471.908389891396
[161.67464472638738, [692077405]]
161.67464472638738
[5740.7570391829295, [280152405]]
5740.7570391829295
[1444.9818322103306, [16899603, 16910037]]
1444.9818322103306
[8338.63349005289, [280145462]]
8338.63349005289
[20.1859742

[2796.643887689095, [16934092]]
2796.643887689095
[10236.015860579506, [16934417]]
10236.015860579506
[11.672198939862415, [16922593]]
11.672198939862415
[130.9627237882145, [321267185]]
130.9627237882145
[3.13544243663613, [5053100]]
3.13544243663613
[1514.666120475588, [16929304]]
1514.666120475588
[1615.2638610667516, [280152405]]
1615.2638610667516
[163.05001102699882, [266255076]]
163.05001102699882
[7074.819432870558, [16878322]]
7074.819432870558
[1509.7660093928534, [16922082]]
1509.7660093928534
[3462.3706487138606, [16906893]]
3462.3706487138606
[740.3587522840533, [16945843]]
740.3587522840533
[805.629540215556, [535528333]]
805.629540215556
[4187.715473632987, [16898233]]
4187.715473632987
[22280.902828964492, [693723608]]
22280.902828964492
[100.76931488053052, [17303647, 535530618]]
100.76931488053052
[101.65801948253511, [17303647, 535530618]]
101.65801948253511
[82.05001194825765, [17303647, 535530618]]
82.05001194825765
[102.2137783648009, [535530618]]
102.213778364800

[7532.598904553969, [280145462]]
7532.598904553969
[22445.551693194586, [16910037]]
22445.551693194586
[12704.92958840297, [393904148]]
12704.92958840297
[4695.365786475332, [280152405]]
4695.365786475332
[6564.70190546275, [372520677]]
6564.70190546275
[826.7005393946811, [969318595]]
826.7005393946811
[116.49577883863455, [541632696]]
116.49577883863455
[7768.600706005071, [512236953]]
7768.600706005071
[14740.039151074578, [16915220]]
14740.039151074578
[15723.569963514426, [280152379]]
15723.569963514426
[4185.895604984415, [17303647, 535530618]]
4185.895604984415
[491.44964681482105, [16929304]]
491.44964681482105
[8169.040091283137, [280152399]]
8169.040091283137
[4083.806335157696, [529605187]]
4083.806335157696
[17190.240477484032, [770413544]]
17190.240477484032
[7197.834769771763, [16915220]]
7197.834769771763
[20897.361329917567, [770413544]]
20897.361329917567
[20919.260315195188, [770413544]]
20919.260315195188
[20900.362113512707, [770413544]]
20900.362113512707
[26466.20

[13470.973899379534, [208426873]]
13470.973899379534
[937.8540512950889, [317355812]]
937.8540512950889
[9844.896985227118, [393016025]]
9844.896985227118
[10235.686421470142, [393015984]]
10235.686421470142
[502.5449280206239, [207592406]]
502.5449280206239
[16.899065137508984, [35342792]]
16.899065137508984
[10697.15126857527, [333433137]]
10697.15126857527
[7472.951020283692, [35342717]]
7472.951020283692
[7471.088571966214, [35342717]]
7471.088571966214
[19.628600551607295, [181751127]]
19.628600551607295
[12274.252371582656, [392545999]]
12274.252371582656
[10250.47693288999, [208426873]]
10250.47693288999
[19527.441006982808, [31054189]]
19527.441006982808
[8943.337149040877, [5663355]]
8943.337149040877
[16751.24881210498, [31054189]]
16751.24881210498
[9844.896985227118, [393016025]]
9844.896985227118
[8.25369148784395, [30118738]]
8.25369148784395
[9057.638358915652, [35342782]]
9057.638358915652
[11515.767543568732, [333433137]]
11515.767543568732
[86.50748845329989, [2861787

distance          IDs  index ML Number  \
0      2818.309440   [37902494]      0  00-00097   
1      9813.136213  [371300246]      1  00-00148   
2      9166.868453   [37447407]      2  00-00189   
3         6.888744  [137333586]      3  00-00222   
4        18.968821  [659616378]      4  00-00245   
...            ...          ...    ...       ...   
3905   1751.133199   [43523795]   3905      None   
3906   3622.989887  [546483224]   3906      None   
3907    797.015166   [35340684]   3907      None   
3908  36042.131013  [693735870]   3908      None   
3909  36009.293490  [693735870]   3909      None   

                               Name     Sex Age Reporting Date  \
0                      Unidentified    male         2000-01-10   
1                    Nicolas, Tomas    male  17     2000-01-22   
2                      Unidentified    male         2000-01-20   
3                      Unidentified    male         2000-01-10   
4     Candia-Bravo, Maria Del Rocio  female  20     2000-02-05   
...                             ...     ...  ..            ...   
3905                           None  Female  10     2021-08-25   
3906                           None    Male  25     2021-08-27   
3907                           None    Male  21     2021-08-30   
3908                           None    Male  31     2021-08-31   
3909                           None    Male  22     2021-08-31   

              Surface Management Location  \
0     Cocopah Indian Reservation            
1               State of Arizona            
2              US Forest Service            
3                        Private            
4           Tohono Oodham Nation            
...                          ...      ...   
3905                        Yuma     None   
3906       Barry Goldwater Range     None   
3907       Barry Goldwater Range     None   
3908               Cabeza Prieta     None   
3909               Cabeza Prieta     None   

                                     Location Precision Corridor Code  \
0     physical description with directions, distance...            12   
1     physical description with directions, distance...             4   
2     physical description with directions, distance...             5   
3     physical description with directions, distance...             9   
4     physical description with directions, distance...             7   
...                                                 ...           ...   
3905                                               None          None   
3906                                               None          None   
3907                                               None          None   
3908                                               None          None   
3909                                               None          None   

        Corridor                    Cause of Death  \
0           Yuma                              None   
1      Patagonia                              None   
2        Nogales                              None   
3            Ajo                              None   
4     San Miguel                              None   
...          ...                               ...   
3905        None        Exposure, high temperature   
3906        None        Exposure, high temperature   
3907        None        Exposure, high temperature   
3908        None  UNDETERMINED - SKELETAL REMAINS    
3909        None  UNDETERMINED - SKELETAL REMAINS    

                                 OME Determined COD Condition Code  \
0     UNDETERMINED - MUMMIFIED AND SKELETAL REMAINS              4   
1                                       HYPOTHERMIA              1   
2                   UNDETERMINED - SKELETAL REMAINS              7   
3                   UNDETERMINED - SKELETAL REMAINS              6   
4                     MULTIPLE BLUNT FORCE INJURIES              1   
...                                             ...            ...   
3905                               

In [19]:
deaths_roads_merged.to_csv('deaths_roads.csv')